In [1]:
import os, sys
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf
from urllib.request import urlretrieve
from collections import OrderedDict
from libs import nb_utils, charrnn, utils

In [2]:
script = 'http://www.awesomefilm.com/script/biglebowski.txt'
txts = []
f, _ = urlretrieve(script, script.split('/')[-1])
with open(f) as fp:
    txt = fp.read()
txt[:100]

'\t\t\tTHE BIG LEBOWSKI\n\n\t\tWe are floating up a steep scrubby slope.  We hear male voices \n\t\tgently sing'

In [3]:
txt = '\n'.join([txt_i.strip() for txt_i 
                 in txt.replace('\t', '').split('\n')
                 if len(txt_i)])
len(txt)

121148

In [4]:
vocab = list(set(txt))
vocab.sort()
len(vocab)

77

In [5]:
vocab

['\n',
 ' ',
 '!',
 '"',
 '%',
 '&',
 "'",
 '(',
 ')',
 ',',
 '-',
 '.',
 '0',
 '1',
 '2',
 '3',
 '4',
 '5',
 '6',
 '7',
 '8',
 '9',
 ':',
 ';',
 '?',
 'A',
 'B',
 'C',
 'D',
 'E',
 'F',
 'G',
 'H',
 'I',
 'J',
 'K',
 'L',
 'M',
 'N',
 'O',
 'P',
 'Q',
 'R',
 'S',
 'T',
 'U',
 'V',
 'W',
 'X',
 'Y',
 'Z',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'q',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z']

In [6]:
encoder = OrderedDict(zip(vocab, range(len(vocab))))
decoder = OrderedDict(zip(range(len(vocab)), vocab))
encoder

OrderedDict([('\n', 0),
             (' ', 1),
             ('!', 2),
             ('"', 3),
             ('%', 4),
             ('&', 5),
             ("'", 6),
             ('(', 7),
             (')', 8),
             (',', 9),
             ('-', 10),
             ('.', 11),
             ('0', 12),
             ('1', 13),
             ('2', 14),
             ('3', 15),
             ('4', 16),
             ('5', 17),
             ('6', 18),
             ('7', 19),
             ('8', 20),
             ('9', 21),
             (':', 22),
             (';', 23),
             ('?', 24),
             ('A', 25),
             ('B', 26),
             ('C', 27),
             ('D', 28),
             ('E', 29),
             ('F', 30),
             ('G', 31),
             ('H', 32),
             ('I', 33),
             ('J', 34),
             ('K', 35),
             ('L', 36),
             ('M', 37),
             ('N', 38),
             ('O', 39),
             ('P', 40),
             ('Q', 41),
 

In [7]:
batch_size = 100

sequence_length = 50

n_cells = 128

n_layers = 3

n_chars = len(vocab)

In [8]:
X = tf.placeholder(tf.int32, (None, sequence_length), 'X')
Y = tf.placeholder(tf.int32, (None, sequence_length), 'Y')

In [9]:
embedding = tf.get_variable('embedding', [n_chars, n_cells])

Xs = tf.nn.embedding_lookup(embedding, X)

Xs.get_shape().as_list()

[None, 50, 128]

In [10]:
with tf.name_scope('reslice'):
    Xs = [tf.squeeze(seq, [1])
          for seq in tf.split(1, sequence_length, Xs)]

In [11]:
cells = tf.nn.rnn_cell.BasicLSTMCell(n_cells, state_is_tuple=True)
cells.state_size

LSTMStateTuple(c=128, h=128)

In [12]:
initial_state = cells.zero_state(tf.shape(X)[0], tf.float32)
initial_state

LSTMStateTuple(c=<tf.Tensor 'zeros:0' shape=(?, 128) dtype=float32>, h=<tf.Tensor 'zeros_1:0' shape=(?, 128) dtype=float32>)

In [14]:
cells = tf.nn.rnn_cell.MultiRNNCell([cells] * n_layers, state_is_tuple=True)
initial_state = cells.zero_state(tf.shape(X)[0], tf.float32)
initial_state

(LSTMStateTuple(c=<tf.Tensor 'zeros_2:0' shape=(?, 128) dtype=float32>, h=<tf.Tensor 'zeros_3:0' shape=(?, 128) dtype=float32>),
 LSTMStateTuple(c=<tf.Tensor 'zeros_4:0' shape=(?, 128) dtype=float32>, h=<tf.Tensor 'zeros_5:0' shape=(?, 128) dtype=float32>),
 LSTMStateTuple(c=<tf.Tensor 'zeros_6:0' shape=(?, 128) dtype=float32>, h=<tf.Tensor 'zeros_7:0' shape=(?, 128) dtype=float32>))

In [14]:
help(tf.nn.rnn)

Help on function rnn in module tensorflow.python.ops.rnn:

rnn(cell, inputs, initial_state=None, dtype=None, sequence_length=None, scope=None)
    Creates a recurrent neural network specified by RNNCell "cell".
    
    The simplest form of RNN network generated is:
      state = cell.zero_state(...)
      outputs = []
      for input_ in inputs:
        output, state = cell(input_, state)
        outputs.append(output)
      return (outputs, state)
    
    However, a few other options are available:
    
    An initial state can be provided.
    If the sequence_length vector is provided, dynamic calculation is performed.
    This method of calculation does not compute the RNN steps past the maximum
    sequence length of the minibatch (thus saving computational time),
    and properly propagates the state at an example's sequence length
    to the final state output.
    
    The dynamic calculation performed is, at time t for batch row b,
      (output, state)(b, t) =
        (t >= 

In [15]:
outputs, state = tf.nn.rnn(cells, Xs, initial_state)
outputs, state

([<tf.Tensor 'RNN/MultiRNNCell/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_1/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_2/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_3/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_4/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_5/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_6/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_7/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_8/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_9/Cell2/BasicLSTMCell/mul_2:0' shape=(?, 128) dtype=float32>,
  <tf.Tensor 'RNN/MultiRNNCell_10/Cell2/BasicLSTMCell/mul_2:0' shape=(?,

In [16]:
outputs_flat = tf.reshape(tf.concat(1, outputs), [-1, n_cells])
outputs_flat

<tf.Tensor 'Reshape:0' shape=(?, 128) dtype=float32>

In [17]:
with tf.variable_scope('prediction'):
    W = tf.get_variable('W', [n_cells, n_chars], 
                        initializer=tf.random_normal_initializer(stddev=.1))
    b = tf.get_variable('b', [n_chars], 
                        initializer=tf.random_normal_initializer(stddev=.1))
    
    logits = tf.matmul(outputs_flat, W) + b
    probs = tf.nn.softmax(logits)
    
    Y_pred = tf.argmax(probs, 1)

In [18]:
with tf.variable_scope('loss'):
    Y_true_flat = tf.reshape(tf.concat(1, Y), [-1])
    loss = tf.nn.sparse_softmax_cross_entropy_with_logits(
        logits, Y_true_flat)
    mean_loss = tf.reduce_mean(loss)

In [19]:
with tf.name_scope('optimizer'):
    optimizer = tf.train.AdamOptimizer(learning_rate=.001)
    gradients = []
    clip = tf.constant(5., name='clip')
    for grad, var in optimizer.compute_gradients(mean_loss):
        gradients.append((tf.clip_by_value(grad, -clip, clip), var))
    updates = optimizer.apply_gradients(gradients)

In [20]:
nb_utils.show_graph(tf.get_default_graph().as_graph_def())

In [22]:
config = tf.ConfigProto(device_count={"GPU": 0})
with tf.Session(config=config) as sess:
    init = tf.initialize_all_variables()
    sess.run(init)
    
    cursor = 0
    it_i = 0
    while it_i <= 500:
        Xs, Ys = [], []
        for batch_i in range(batch_size):
            if cursor + sequence_length >= len(txt) - sequence_length - 1:
                cursor = 0
            Xs.append([encoder[ch] for ch in txt[cursor:cursor+sequence_length]])
            Ys.append([encoder[ch] for ch in txt[cursor+1:cursor+sequence_length+1]])
            cursor = cursor + sequence_length
        Xs = np.array(Xs).astype(np.int32)
        Ys = np.array(Ys).astype(np.int32)
        
        loss_val, _ = sess.run([mean_loss, updates], feed_dict={X: Xs, Y: Ys})
        
        if it_i % 100 == 0:
            print(it_i, loss_val)
            
        if it_i % 500 == 0:
            p = sess.run(probs, feed_dict={X: Xs[-1][np.newaxis]})
            ps = [np.random.choice(range(n_chars), p=p_i.ravel()) for p_i in p]
            p = [np.argmax(p_i) for p_i in p]
            if isinstance(txt[0], str):
                print('original:', "".join([decoder[ch] for ch in Xs[-1]]))
                print('synth(samp):', ''.join([decoder[ch] for ch in ps]))
                print('synth(amax):', ''.join([decoder[ch] for ch in p]))
            else:
                print([decoder[ch] for ch in ps])
        it_i += 1

0 4.3513
original: kie Treehorn, that
means you owe money to Jackie
T
synth(samp): X&d8N8'&Bi1pYdJk-loc&jCzPC1NEB6gv'IpU?4 zsHx!vay0'
synth(amax): ccccccccccccccccccccdddddccccccccccccccccccccHHHHH
100 3.42122
200 3.0213
300 2.7883
400 2.59207
500 2.51971
original: 's video, Dude.  Now that we're
competing with the
synth(samp): eetegemf aamn.
TWda,veet to'm, tlm.othvr bocea,ho 
synth(amax): t tene r thde 
 Te  then to te toueer ng tonhethe 


In [23]:
tf.reset_default_graph()

In [24]:
with open('trump.txt') as fp:
    txt = fp.read()
txt[:100]

'me today this was going to be a speech on hillary clinton and all of the bad things and we all know '

In [25]:
words = set(txt.split(' '))
words

{'',
 'steinly?',
 'media',
 'programming',
 'movies',
 'extend',
 'secondly,',
 'anymore',
 'undefeated',
 'bride',
 'aspects',
 'permit',
 'power',
 'testing',
 'committed',
 'seventies',
 'horribly',
 'full',
 'plants',
 'atrophy',
 'phones',
 'sp',
 'view,',
 '$64',
 'used',
 'mitt',
 'hopefully',
 'crimes.',
 'terrific',
 'crowd',
 'healthcare',
 'job-killing',
 'levels',
 'fraud',
 'twice',
 'dishonorable',
 'continued',
 'nra',
 'extent',
 'initiatives',
 '7th',
 'enriched',
 'excited',
 'safe.',
 'frequently',
 'uss',
 'brother,',
 'seal',
 'high-crime',
 'passing',
 'companies.',
 'through',
 "boeing's",
 'sources',
 'delighted',
 'pity',
 'sending',
 'big-league',
 'ineptitude',
 '1080',
 "network's",
 'folks',
 'cited',
 'reiterated',
 'heed',
 'avoid',
 'sharia',
 'excitement',
 'buttes',
 'trails',
 'movement',
 'arizona',
 'sylvania',
 'republic.',
 'semi',
 'liners',
 'flag',
 'stroked',
 'off,',
 'treatment',
 'stupid',
 'big.',
 'summer',
 'glass',
 'girl',
 'plate',
 

In [26]:
counts = {word_i: 0 for word_i in words}
for word_i in txt.split(' '):
    counts[word_i] += 1
counts

{'': 2,
 'kept': 13,
 'blitzer': 1,
 'steinly?': 1,
 'opponents': 2,
 'media': 30,
 'movies': 1,
 'extend': 4,
 'independence.': 1,
 'secondly,': 2,
 'anymore': 71,
 'provocative': 1,
 'step': 7,
 'certainly': 16,
 'fourth,': 2,
 'mosques': 6,
 'undefeated': 4,
 'trafficking': 1,
 'jus': 1,
 'won': 72,
 'bride': 3,
 'exploration': 4,
 'aspects': 1,
 'amended': 1,
 'permit': 13,
 'plum': 1,
 'destructive': 3,
 'power': 84,
 'featuring': 1,
 'shifted': 1,
 'programming': 2,
 'shop': 3,
 'reduction': 4,
 'committed': 7,
 'garden': 2,
 'seventies': 1,
 'deductibles': 4,
 'founder': 10,
 'other': 345,
 'horribly': 11,
 'full': 37,
 'plants': 31,
 'phones': 4,
 'sp': 1,
 'knees': 1,
 'services': 13,
 'view,': 1,
 '$64': 1,
 'automobile': 1,
 'used': 72,
 'mitt': 3,
 'prosecutors': 1,
 'hopefully': 9,
 'crimes.': 1,
 'terrific': 12,
 'crowd': 20,
 'recovered': 2,
 'satellites': 1,
 'interested': 6,
 'healthcare': 6,
 'naming': 2,
 'job-killing': 6,
 '802': 1,
 'mean': 250,
 'levels': 5,
 '27-

In [27]:
[(word_i, counts[word_i]) for word_i in sorted(counts, key=counts.get, reverse=True)]

[('the', 7404),
 ('and', 7199),
 ('to', 6079),
 ('i', 4551),
 ('a', 4269),
 ('of', 3990),
 ('you', 3441),
 ('we', 3373),
 ('that', 2900),
 ('in', 2654),
 ('have', 2441),
 ('it', 2360),
 ('they', 2149),
 ('is', 2008),
 ('so', 1721),
 ('our', 1654),
 ('going', 1595),
 ('but', 1543),
 ('people', 1538),
 ('be', 1489),
 ('this', 1452),
 ('for', 1387),
 ('know', 1307),
 ('was', 1274),
 ("we're", 1200),
 ('are', 1181),
 ('with', 1170),
 ('will', 1151),
 ('not', 1109),
 ('what', 1094),
 ('all', 1004),
 ("it's", 998),
 ('do', 987),
 ("don't", 936),
 ('on', 927),
 ('said', 916),
 ('he', 907),
 ('want', 783),
 ('great', 771),
 ('because', 747),
 ('about', 730),
 ('one', 726),
 ('right', 699),
 ('like', 699),
 ('just', 694),
 ('very', 682),
 ("that's", 675),
 ('get', 673),
 ('she', 667),
 ('country', 659),
 ('me', 656),
 ('at', 641),
 ('by', 638),
 ("i'm", 631),
 ('if', 624),
 ('now', 619),
 ('gonna', 606),
 ('out', 585),
 ('as', 585),
 ('when', 565),
 ('say', 548),
 ('these', 547),
 ('from', 532)

In [28]:
ckpt_name = 'trump.ckpt'
g = tf.Graph()
n_layers = 3
n_cells = 512
with tf.Session(graph=g) as sess, g.device('/cpu:0'):
    model = charrnn.build_model(txt=txt,
                                batch_size=1,
                                n_layers=n_layers,
                                n_cells=n_cells,
                                gradient_clip=10.0)
    saver = tf.train.Saver()
    if os.path.exists(ckpt_name):
        saver.restore(sess, ckpt_name)
        print("Model restored.")

Model restored.


In [29]:
nb_utils.show_graph(g.as_graph_def())

In [34]:
n_iterations = 100
curr_states = None
g = tf.Graph()
with tf.Session(graph=g) as sess, g.device('/cpu:0'):
    model = charrnn.build_model(txt=txt,
                                batch_size=1,
                                sequence_length=1,
                                n_layers=n_layers,
                                n_cells=n_cells,
                                gradient_clip=10.)
    saver = tf.train.Saver()
    if os.path.exists(ckpt_name):
        saver.restore(sess, ckpt_name)
        print("Model restored.")
        
    init_states = []
    for s_i in model['initial_state']:
        init_states.append(s_i.c)
        init_states.append(s_i.h)
        
    final_states = []
    for s_i in model['final_state']:
        final_states.append(s_i.c)
        final_states.append(s_i.h)
        
    synth = [[encoder[' ']]]
    for i in range(n_iterations):
        
        feed_dict = {model['X']: [synth[-1]],
                     model['keep_prob']: 1.}
        
        if curr_states:
            feed_dict.update({init_state_i: curr_state_i for 
                              (init_state_i, curr_state_i) in 
                              zip(init_states, curr_states)})
            
        p = sess.run(model['probs'], feed_dict=feed_dict)[0]
        
        curr_states = sess.run(final_states, feed_dict=feed_dict)
        
        p = np.argmax(p)
        
        synth.append([p])
        
        print(model['decoder'][p], end='')
        sys.stdout.flush()

Model restored.
the world trade organization nafta was the worst trade deal in the history it's like the history of 

In [38]:
curr_states = None
g = tf.Graph()
with tf.Session(graph=g) as sess, g.device('/cpu:0'):
    model = charrnn.build_model(txt=txt,
                                batch_size=1,
                                sequence_length=1,
                                n_layers=n_layers,
                                n_cells=n_cells,
                                gradient_clip=10.)
    saver = tf.train.Saver()
    if os.path.exists(ckpt_name):
        saver.restore(sess, ckpt_name)
        print("Model restored.")
        
    init_states = []
    for s_i in model['initial_state']:
        init_states.append(s_i.c)
        init_states.append(s_i.h)
        
    final_states = []
    for s_i in model['final_state']:
        final_states.append(s_i.c)
        final_states.append(s_i.h)
        
    synth = [[encoder[' ']]]
    for i in range(n_iterations):
        
        feed_dict = {model['X']: [synth[-1]],
                     model['keep_prob']: 1.}
        
        if curr_states:
            feed_dict.update({init_state_i: curr_state_i for
                              (init_state_i, curr_state_i) in 
                              zip(init_states, curr_states)})
            
        p = sess.run(model['probs'], feed_dict=feed_dict)[0]
        
        curr_states = sess.run(final_states, feed_dict=feed_dict)
        
        p = p.astype(np.float64)
        p = np.random.multinomial(1, p.ravel() / p.sum())
        p = np.argmax(p)
        
        synth.append([p])
        
        print(model['decoder'][p], end='')
        sys.stdout.flush()

Model restored.
hurt the polls we got a beater she would be a disaster remember this justices of the united states s

In [40]:
temperature = .5
curr_states = None
g = tf.Graph()
with tf.Session(graph=g) as sess, g.device('/cpu:0'):
    model = charrnn.build_model(txt=txt,
                                batch_size=1,
                                sequence_length=1,
                                n_layers=n_layers,
                                n_cells=n_cells,
                                gradient_clip=10.)
    saver = tf.train.Saver()
    if os.path.exists(ckpt_name):
        saver.restore(sess, ckpt_name)
        print("Model restored.")
        
    init_states = []
    for s_i in model['initial_state']:
        init_states.append(s_i.c)
        init_states.append(s_i.h)
        
    final_states = []
    for s_i in model['final_state']:
        final_states.append(s_i.c)
        final_states.append(s_i.h)
        
    synth = [[encoder[' ']]]
    for i in range(n_iterations):
        
        feed_dict = {model['X']: [synth[-1]],
                     model['keep_prob']: 1.}
        
        if curr_states:
            feed_dict.update({init_state_i: curr_state_i for
                              (init_state_i, curr_state_i) in
                              zip(init_states, curr_states)})
            
        p = sess.run(model['probs'], feed_dict=feed_dict)[0]
        
        curr_states = sess.run(final_states, feed_dict=feed_dict)
        
        p = p.astype(np.float64)
        p = np.log(p) / temperature
        p = np.exp(p) / np.sum(np.exp(p))
        p = np.random.multinomial(1, p.ravel() / p.sum())
        p = np.argmax(p)
        
        synth.append([p])
        
        print(model['decoder'][p], end='')
        sys.stdout.flush()

Model restored.
we have a lot of the countries in nato they're not paying us is supposed to be paying us they're not

In [42]:
prime = 'obama'
temperature = 1.
curr_states = None
n_iterations = 500
g = tf.Graph()
with tf.Session(graph=g) as sess, g.device('/cpu:0'):
    model = charrnn.build_model(txt=txt,
                                batch_size=1,
                                sequence_length=1,
                                n_layers=n_layers,
                                n_cells=n_cells,
                                gradient_clip=10.)
    saver = tf.train.Saver()
    if os.path.exists(ckpt_name):
        saver.restore(sess, ckpt_name)
        print("Model restored.")
        
    init_states = []
    for s_i in model['initial_state']:
        init_states.append(s_i.c)
        init_states.append(s_i.h)
        
    final_states = []
    for s_i in model['final_state']:
        final_states.append(s_i.c)
        final_states.append(s_i.h)
        
    curr_states = None
    for ch in prime:
        feed_dict = {model['X']: [[model['encoder'][ch]]],
                     model['keep_prob']: 1.}
        if curr_states:
            feed_dict.update({init_state_i: curr_state_i for 
                              (init_state_i, curr_state_i) in
                              zip(init_states, curr_states)})
            
        p = sess.run(model['probs'], feed_dict=feed_dict)[0]
        p = p.astype(np.float64)
        p = np.log(p) / temperature
        p = np.exp(p) / np.sum(np.exp(p))
        p = np.random.multinomial(1, p.ravel() / p.sum())
        p = np.argmax(p)
        
        curr_states = sess.run(final_states, feed_dict=feed_dict)
        
    synth = [[p]]
    print(prime + model['decoder'][p], end='')
    for i in range(n_iterations):
        
        feed_dict = {model['X']: [synth[-1]],
                     model['keep_prob']: 1.}
        
        feed_dict.update({init_state_i: curr_state_i for
                          (init_state_i, curr_state_i) in
                          zip(init_states, curr_states)})
        
        p = sess.run(model['probs'], feed_dict=feed_dict)[0]
        
        curr_states = sess.run(final_states, feed_dict=feed_dict)
        
        p = p.astype(np.float64)
        p = np.log(p) / temperature
        p = np.exp(p) / np.sum(np.exp(p))
        p = np.random.multinomial(1, p.ravel() / p.sum())
        p = np.argmax(p)
        
        synth.append([p])
        
        print(model['decoder'][p], end='')
        sys.stdout.flush()

Model restored.
obama change ok americans are the people that can't afford that we're going to take care of them and i tell you what i've never had one person and i have the biggest crowds of anybody i've never had one person stand up and say that's not republican let me tell you it is republican folks you know every time i've ever said it i've never had anybody other than the egg kids you know the people that said trump is never gonna run and he runs i don't think he'll do very well we go to six we got 12 12 24 we g

In [2]:
utils.build_submission('session-5.zip',
                       ('vaegan.gif',
                        'session-5-part-1.ipynb',
                        'session-5-part-2.ipynb'))

Your assignment zip file has been created!
Now submit the file:
/Users/km/MEGA/notebooks/kadenze/CADL/session-5/session-5.zip
to Kadenze for grading!
